In [ ]:
# Install mysql module
!pip3.9 install mysql-connector-python
!pip3.9 install pandas

In [ ]:
# Make sure ur IP is on file
!curl ipecho.net/plain

In [1]:
# Connect to server
import mysql.connector
import random
import pandas as pd

mydb = mysql.connector.connect(
    host="35.232.56.109",
    user="root",
    password="ah08EbAGxF04I503",
    database="SpotifyHelpr"
)

mycursor = mydb.cursor()

In [2]:
# Load CSV
df = pd.read_csv("SpotifyFeatures.csv")
ids = df.track_id.tolist()

# Get 1000 most popular songs
df2 = df.drop_duplicates(subset=["track_id"]).sort_values("popularity",ascending=False)

In [3]:
# Print results from query
def print_cursor(cursor):
    myresult = cursor.fetchall()
    for x in myresult:
        print(x)

In [4]:
# Commit changes to server
def commit():
    mydb.commit()

In [ ]:
# Create Users table
mycursor.execute("""CREATE TABLE Users (
	userId   INT         NOT NULL,
	userName VARCHAR(50),
	password VARCHAR(50),
	apiToken VARCHAR(50),

	PRIMARY KEY(userId)
);""")

In [ ]:
# Populate Users table
for i in range(1009):
    mycursor.execute(f'Insert into Users Values({i+1}, "test{i+1}", "pwd", "api{i+1}");')

In [ ]:
# Create the Songs table
mycursor.execute("""CREATE TABLE Songs (
	songId         VARCHAR(50) NOT NULL,
	name           VARCHAR(150),
	artist         VARCHAR(50),
	genre          VARCHAR(50),
	url            VARCHAR(50),
	likenessFactor REAL,

	PRIMARY KEY(songId)
);""")

In [ ]:
# Populate Songs table
# idx = -1
completed = 22439
amt = 25000

to_add = df2.head(completed+amt).tail(amt)
l = []

for i, entry in to_add.iterrows():
    # idx += 1
    # if idx < 134:
    #     continue
    try:
        entry = list(entry)
        url = f"open.spotify.com/track/{entry[3]}"
        entry2 = entry[2].replace('"', '')
        mycursor.execute(f'Insert into Songs Values("{entry[3]}", "{entry2}", "{entry[1]}", "{entry[0]}", "{url}", {random.randint(1, 20)});')
        commit()
    except:
        continue

In [ ]:
# Create the Reviews table
mycursor.execute("""CREATE TABLE Reviews (
	reviewId INT          NOT NULL,
	rating   REAL,
	body     VARCHAR(140),

	songId   VARCHAR(50),
	userId   INT,

	PRIMARY KEY(reviewId),
	FOREIGN KEY(songId) REFERENCES Songs(songId) ON DELETE CASCADE,
	FOREIGN KEY(userId) REFERENCES Users(userId) ON DELETE CASCADE
);""")

In [ ]:
# Populate Reviews table
l=[]
d = {}
idx = 0
for i, entry in df2head.iterrows():
    d[idx] = entry[3]
    idx += 1

for i in range(1000):
    f = [d[random.randint(0, 999)], random.randint(0, 1000)]
    while(f in l):
        f = [d[random.randint(0, 999)], random.randint(0, 1000)]

    l.append(f)

    mycursor.execute(f'insert into Reviews values({i}, {random.randint(0, 10)}, "body{i}", "{f[0]}", {f[1]});')
    commit()

In [ ]:
# Create Playlists table
mycursor.execute("""CREATE TABLE Playlists (
	playlistId   INT         NOT NULL,
	playlistName VARCHAR(50),

	userId       INT,

	PRIMARY KEY(playlistId),
	FOREIGN KEY(userId) REFERENCES Users(userId) ON DELETE CASCADE
);""")

In [ ]:
# Populate Playlists table
for i in range(1000):
    mycursor.execute(f'Insert into Playlists Values({i}, "playlist{i}", {random.randint(0, 1000)});')
    commit()

In [ ]:
# Create SongsFoundIn table
mycursor.execute("""CREATE TABLE SongsFoundIn (
	songId     VARCHAR(50) NOT NULL,
	playlistId INT         NOT NULL,

	PRIMARY KEY(songId, playlistId),
	FOREIGN KEY(songId)     REFERENCES Songs(songId)         ON DELETE CASCADE,
	FOREIGN KEY(playlistId) REFERENCES Playlists(playlistId) ON DELETE CASCADE
);""")

In [ ]:
# Populate SongsFoundIn table
d = {}
idx = 0
for i, entry in df2head.iterrows():
    d[idx] = entry[3]
    idx += 1

for i in range(1000):
    l = []
    for j in range(random.randint(3, 8)):
        f = d[random.randint(0, 999)]
        while(f in l):
            f = d[random.randint(0, 999)]

        l.append(f)
        mycursor.execute(f'Insert into SongsFoundIn Values("{f}", {i});')
        commit()

In [ ]:
# Create table Friends
mycursor.execute("""CREATE TABLE Friends (
	friendId INT  NOT NULL,
	userId   INT  NOT NULL,
	fScore   REAL,

	PRIMARY KEY(friendId, userId),
	FOREIGN KEY(friendId) REFERENCES Users(userId) ON DELETE CASCADE,
	FOREIGN KEY(userId)   REFERENCES Users(userId) ON DELETE CASCADE
);""")

In [ ]:
# Create random friendships

friendships = []
for i in range(2000):
    f1 = random.randint(0, 999)
    f2 = random.randint(0, 999)
    while(f1 == f2):
        f2 = random.randint(0, 999)

    l = [f1, f2]
    l2 = [f2, f1]

    if l not in friendships and l2 not in friendships:
        mycursor.execute(f'Insert into Friends Values({l[1]}, {l[0]}, {random.randint(1, 10)});')
        friendships.append(l)
        

In [ ]:
# Find the name, artist, and average ratings for all the songs in a given playlist (eg. playlistId 700)
query = """SELECT name, artist, r.avg_rating
FROM Songs
NATURAL JOIN (SELECT songId FROM SongsFoundIn WHERE playlistId = 700) s
LEFT JOIN (SELECT songId, avg(rating) AS avg_rating FROM Reviews GROUP BY songId) r
ON Songs.songId = r.songId;"""

mycursor.execute(query) # Find the name, artist, and average ratings for all the songs in a given playlist (eg. playlistId 700)
print_cursor(mycursor)

In [ ]:
# Find the username, song name, artist, body, and ratings for all the reviews written by all of a User's friends (eg. userId = 90). We are using a UNION in order to find occurrences where the user is a friend of another user (as our friends relations are directed)
query = """SELECT Users.userName, sub.name, sub.artist, sub.body, sub.rating
FROM 
(SELECT Reviews.userId, Songs.name, Songs.artist, Reviews.body, Reviews.rating
	FROM Songs NATURAL JOIN Reviews) sub
JOIN Users ON Users.userId = sub.UserId
WHERE sub.userId IN (SELECT friendId FROM Friends WHERE userId = 90) 

UNION

SELECT Users.userName, sub.name, sub.artist, sub.body, sub.rating
FROM
(SELECT Reviews.userId, Songs.name, Songs.artist, Reviews.body, Reviews.rating
	FROM Songs NATURAL JOIN Reviews) sub 
JOIN Users ON Users.userId = sub.UserId
WHERE sub.userId IN (SELECT userId FROM Friends WHERE friendId = 90);"""

mycursor.execute(query) 
print_cursor(mycursor)

In [ ]:
query = """SELECT * from Songs;"""

mycursor.execute(query) 
l=[]  # Stores all playlistIds of a User
print_cursor(mycursor)

In [ ]:
query = """SELECT COUNT(*) from Songs;"""

mycursor.execute(query) 
l=[]  # Stores all playlistIds of a User
print_cursor(mycursor)

In [ ]:
query = """SELECT playlistId FROM Playlists WHERE userId = 90;"""

mycursor.execute(query) 
l=[]  # Stores all playlistIds of a User
# print_cursor(mycursor)
myresult = mycursor.fetchall()
for x in myresult:
    l.append(x[0])


for i in l:
    
    print(i)
    query = f"""SELECT * FROM Songs WHERE songId IN (SELECT songId FROM SongsFoundIn WHERE playlistId = {i})"""

    mycursor.execute(query) 
    print_cursor(mycursor)

In [ ]:
# Find the name, artist, and average ratings for all the songs in a given playlist (eg. playlistId 700)
query = """SELECT name, artist, r.avg_rating
FROM Songs
NATURAL JOIN (SELECT songId FROM SongsFoundIn WHERE playlistId = 0) s
LEFT JOIN (SELECT songId, avg(rating) AS avg_rating FROM Reviews GROUP BY songId) r
ON Songs.songId = r.songId;"""

#mycursor.execute("SHOW INDEX FROM Users")
mycursor.execute(query)
# mycursor.execute("ALTER TABLE Users ADD INDEX (userName);")  # Find the name, artist, and average ratings for all the songs in a given playlist (eg. playlistId 700)
print_cursor(mycursor)

In [5]:
mycursor.execute("SHOW INDEX FROM Users")
print_cursor(mycursor)

('Users', 0, 'PRIMARY', 1, 'userId', 'A', 1000, None, None, '', 'BTREE', '', '', 'YES', None)
('Users', 1, 'userName', 1, 'userName', 'A', 1000, None, None, 'YES', 'BTREE', '', '', 'YES', None)
('Users', 1, 'userName_2', 1, 'userName', 'A', 1000, None, None, 'YES', 'BTREE', '', '', 'YES', None)
('Users', 1, 'userName_3', 1, 'userName', 'A', 1000, None, None, 'YES', 'BTREE', '', '', 'YES', None)
('Users', 1, 'userName_4', 1, 'userName', 'A', 1000, None, None, 'YES', 'BTREE', '', '', 'YES', None)
('Users', 1, 'userName_5', 1, 'userName', 'A', 1000, None, None, 'YES', 'BTREE', '', '', 'YES', None)
('Users', 1, 'userName_6', 1, 'userName', 'A', 1000, None, None, 'YES', 'BTREE', '', '', 'YES', None)


In [6]:
import pandas as pd
from sklearn.cluster import KMeans
import numpy as np

df_kMeans = pd.read_csv("SpotifyFeatures.csv")

track_ids = df_kMeans['track_id'].copy()
df_kMeans = df_kMeans.drop(['track_id', 'genre', 'artist_name', 'track_name', 'key', 'mode', 'time_signature'], axis=1)

X = np.array(df_kMeans)
k = KMeans(n_clusters=10, random_state=0).fit(X)
df_kMeans['track_id'] = track_ids
df_kMeans['likeness_factor'] = k.labels_
df_kMeans.astype({'likeness_factor': 'float64'})

popularity  acousticness  danceability  duration_ms  energy  \
0                0       0.61100         0.389        99373   0.910   
1                1       0.24600         0.590       137373   0.737   
2                3       0.95200         0.663       170267   0.131   
3                0       0.70300         0.240       152427   0.326   
4                4       0.95000         0.331        82625   0.225   
...            ...           ...           ...          ...     ...   
232720          39       0.00384         0.687       326240   0.714   
232721          38       0.03290         0.785       282447   0.683   
232722          47       0.90100         0.517       166960   0.419   
232723          44       0.26200         0.745       222442   0.704   
232724          35       0.09730         0.758       323027   0.470   

        instrumentalness  liveness  loudness  speechiness    tempo  valence  \
0               0.000000    0.3460    -1.828       0.0525  166.969    0.814   
1               0.000000    0.1510    -5.559       0.0868  174.003    0.816   
2               0.000000    0.1030   -13.879       0.0362   99.488    0.368   
3               0.000000    0.0985   -12.178       0.0395  171.758    0.227   
4               0.123000    0.2020   -21.150       0.0456  140.576    0.390   
...                  ...       ...       ...          ...      ...      ...   
232720          0.544000    0.0845   -10.626       0.0316  115.542    0.962   
232721          0.000880    0.2370    -6.944       0.0337  113.830    0.969   
232722          0.000000    0.0945    -8.282       0.1480   84.135    0.813   
232723          0.000000    0.3330    -7.137       0.1460  100.031    0.489   
232724          0.000049    0.0836    -6.708       0.0287  113.897    0.479   

                      track_id  likeness_factor  
0       0BRjO6ga9RKCKjfDqeFgWV              6.0  
1       0BjC1NfoEOOusryehmNudP              1.0  
2       0CoSDzoNIKCRs124s9uTVy              1.0  
3       0Gc6TVm52BwZD07Ki6tIvf              1.0  
4       0IuslXpMROHdEPvSl1fTQK              6.0  
...                        ...              ...  
232720  2XGLdVl7lGeq8ksM6Al7jT              7.0  
232721  1qWZdkBl4UVPj9lK6HuuFM              0.0  
232722  2ziWXUmQLrXTiYjCg2fZ2t              1.0  
232723  6EFsue2YbIG4Qkq8Zr9Rir              5.0  
232724  34XO9RwPMKjbvRry54QzWn              7.0  

[232725 rows x 13 columns]

In [7]:
likeness_dict = df_kMeans.set_index('track_id').to_dict()['likeness_factor']
# print(likeness_dict)

In [8]:
(unique, counts) = np.unique(k.labels_, return_counts=True)
frequencies = np.asarray((unique, counts)).T
print(frequencies)

[[    0 46232]
 [    1 59486]
 [    2   290]
 [    3  6314]
 [    4    45]
 [    5 78925]
 [    6 22079]
 [    7 17949]
 [    8    64]
 [    9  1341]]


In [14]:
import numpy as np

mycursor.execute("""SELECT songId FROM Songs """)
sql_query = []

myresult = mycursor.fetchall()
for x in myresult:
    sql_query.append(x[0])
    
for i in sql_query:
    query = f'''
        UPDATE Songs
        SET likenessFactor = {likeness_dict[i]}
        WHERE songId = '{i}';
    '''
    mycursor.execute(query)
    commit()

In [16]:
mycursor.execute(f"""SELECT * FROM Songs""")
print_cursor(mycursor)

('000xQL6tZNLJzIrtIgxqSl', 'Still Got Time', 'ZAYN', 'Dance', 'open.spotify.com/track/000xQL6tZNLJzIrtIgxqSl', 1.0)
('001gDjxhKGDSx4sMMAgS9R', 'Kingdom', 'Young Tribe', 'Children’s Music', 'open.spotify.com/track/001gDjxhKGDSx4sMMAgS9R', 5.0)
('002opcRBgYV5jqoh72QcqA', 'Just to See You Smile', "Why Don't We", 'Dance', 'open.spotify.com/track/002opcRBgYV5jqoh72QcqA', 1.0)
('002QT7AS6h1LAF5dla8D92', 'Still Smell Like It', 'Young Dolph', 'Hip-Hop', 'open.spotify.com/track/002QT7AS6h1LAF5dla8D92', 5.0)
('002r1ZwqA9IL2pWtJMOs9f', "Worryin' Bout Me", 'BJ The Chicago Kid', 'Alternative', 'open.spotify.com/track/002r1ZwqA9IL2pWtJMOs9f', 5.0)
('003eoIwxETJujVWmNFMoZy', 'Growing Pains', 'Alessia Cara', 'Dance', 'open.spotify.com/track/003eoIwxETJujVWmNFMoZy', 1.0)
('004rT6Xq1OS7Db8dncwY2F', 'Supa Nova', 'Green Assassin Dollar', 'Jazz', 'open.spotify.com/track/004rT6Xq1OS7Db8dncwY2F', 6.0)
('005lwxGU1tms6HGELIcUv9', 'I Kissed A Girl', 'Katy Perry', 'Dance', 'open.spotify.com/track/005lwxGU1tms6HG

In [11]:
likeness_dict['00cn1ynXQhURwsgv69fN0b']

5